### Importing libraries

In [1]:
import pandas as pd
import numpy as np
import os
from random import randrange
import string as st
import re
from nltk import WordNetLemmatizer
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
nltk.download('wordnet')
from nltk import WordNetLemmatizer

[nltk_data] Downloading package stopwords to /home/vedant/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/vedant/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


### Loading Data

In [2]:
data_path = "../BBC News Summary/"

os.listdir(data_path)

['News Articles', 'Summaries']

In [3]:
def load_data(path):
    articlesp = path + "News Articles/"
    summariesp = path + "Summaries/"
    data_json = {"News Articles":[],"Summaries":[],"Category":[],"Unlike" : []}
    for i in os.listdir(articlesp):
        a = os.listdir(articlesp+i)
        s = os.listdir(summariesp+i)
        for j in range(len(a)):
            with open(articlesp+i+"/"+a[j]) as fp:
                data_json["News Articles"].append(fp.read())
            with open(summariesp+i+"/"+s[j]) as fp:
                data_json["Summaries"].append(fp.read())
            data_json["Category"].append(i)
    
    for i in range(len(data_json["Summaries"])):
        x = randrange(len(data_json["Summaries"]))
        while data_json["Category"][x] == data_json["Category"][i]:
            x = randrange(len(data_json["Summaries"]))
        data_json["Unlike"].append(data_json["News Articles"][x])
    return data_json

In [4]:
load_data(data_path)

{'News Articles': ["Who do you think you are?\n\nThe real danger is not what happens to your data as it crosses the net, argues analyst Bill Thompson. It is what happens when it arrives at the other end.\n\nThe Financial Services Authority has warned banks and other financial institutions that members of criminal gangs may be applying for jobs which give them access to confidential customer data. The fear is not that they will steal money from our bank accounts but that they will instead steal something far more valuable in our digital society - our identities. Armed with the personal details that a bank holds, plus a fake letter or two, it is apparently easy to get a loan, open a bank account with an overdraft or get a credit card in someone else's name. And it is then a simple matter to move the money into another account and leave the unwitting victim to sort out the mess when statements and demands for payment start arriving. Identity theft is an increasingly significant economic c

In [5]:
data = pd.DataFrame(load_data(data_path))
data

News Articles  \
0     Who do you think you are?\n\nThe real danger i...   
1     Fast moving phone viruses appear\n\nSecurity f...   
2     Seamen sail into biometric future\n\nThe luxur...   
3     Cable offers video-on-demand\n\nCable firms NT...   
4     How to make a greener computer\n\nThe hi-tech ...   
...                                                 ...   
2220  Circuit City gets takeover offer\n\nCircuit Ci...   
2221  German business confidence slides\n\nGerman bu...   
2222  Wal-Mart fights back at accusers\n\nTwo big US...   
2223  Economy 'stronger than forecast'\n\nThe UK eco...   
2224  US Airways staff agree to pay cut\n\nA union r...   

                                              Summaries  Category  \
0     But, however careful you may be, if the organi...      tech   
1     The new strains of the Cabir mobile phone viru...      tech   
2     She said French, Jordanian and Nigerian nation...      tech   
3     Cable firms NTL and Telewest have both launche...      tech   
4     We're seeing the same thing in the technology ...      tech   
...                                                 ...       ...   
2220  Bill Armstrong, a retail analyst at CL King & ...  business   
2221  Analysts said that the Ifo figures and Germany...  business   
2222  Meanwhile, drugs group Eli Lilly is planning a...  business   
2223  "The MPC judges that overall growth was a litt...  business   
2224  The seventh largest carrier in the US sought b...  business   

                                                 Unlike  
0     Top gig award for Scissor Sisters\n\nNew York ...  
1     Black Sabbath top rock album poll\n\nBlack Sab...  
2     Farrell due to make US TV debut\n\nActor Colin...  
3     US firm 'bids for Lacroix label'\n\nA US firm ...  
4     Stars pay tribute to actor Davis\n\nHollywood ...  
...                                                 ...  
2220  Saint-Andre anger at absent stars\n\nSale Shar...  
2221  McConnell in 'drunk' remark row\n\nScotland's ...  
2222  Ray DVD beats box office takings\n\nOscar-nomi...  
2223  Whitehall cuts 'ahead of target'\n\nThousands ...  
2224  Beattie return calms attack fears\n\nEverton s...  

[2225 rows x 4 columns]

### Data exploration and Preprocessing

In [6]:
data.drop("Category", axis=1, inplace=True)
data

News Articles  \
0     Who do you think you are?\n\nThe real danger i...   
1     Fast moving phone viruses appear\n\nSecurity f...   
2     Seamen sail into biometric future\n\nThe luxur...   
3     Cable offers video-on-demand\n\nCable firms NT...   
4     How to make a greener computer\n\nThe hi-tech ...   
...                                                 ...   
2220  Circuit City gets takeover offer\n\nCircuit Ci...   
2221  German business confidence slides\n\nGerman bu...   
2222  Wal-Mart fights back at accusers\n\nTwo big US...   
2223  Economy 'stronger than forecast'\n\nThe UK eco...   
2224  US Airways staff agree to pay cut\n\nA union r...   

                                              Summaries  \
0     But, however careful you may be, if the organi...   
1     The new strains of the Cabir mobile phone viru...   
2     She said French, Jordanian and Nigerian nation...   
3     Cable firms NTL and Telewest have both launche...   
4     We're seeing the same thing in the technology ...   
...                                                 ...   
2220  Bill Armstrong, a retail analyst at CL King & ...   
2221  Analysts said that the Ifo figures and Germany...   
2222  Meanwhile, drugs group Eli Lilly is planning a...   
2223  "The MPC judges that overall growth was a litt...   
2224  The seventh largest carrier in the US sought b...   

                                                 Unlike  
0     Top gig award for Scissor Sisters\n\nNew York ...  
1     Black Sabbath top rock album poll\n\nBlack Sab...  
2     Farrell due to make US TV debut\n\nActor Colin...  
3     US firm 'bids for Lacroix label'\n\nA US firm ...  
4     Stars pay tribute to actor Davis\n\nHollywood ...  
...                                                 ...  
2220  Saint-Andre anger at absent stars\n\nSale Shar...  
2221  McConnell in 'drunk' remark row\n\nScotland's ...  
2222  Ray DVD beats box office takings\n\nOscar-nomi...  
2223  Whitehall cuts 'ahead of target'\n\nThousands ...  
2224  Beattie return calms attack fears\n\nEverton s...  

[2225 rows x 3 columns]

Category was dropped here because category isn't relevant to the project. If, in future an attempt is made to parametrize answers, then the category column will be necessary

In [7]:
def to_lower(text):
    return text.lower()

In [8]:
data["Lower News Articles"] = data["News Articles"].apply(to_lower)
data["Lower Summary"] = data["Summaries"].apply(to_lower)
data["Lower Unlike"] = data["Unlike"].apply(to_lower)

data.head()

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  
0  top gig award for scissor sisters\n\nnew york ...  
1  black sabbath top rock album poll\n\nblack sab...  
2  farrell due to make us tv debut\n\nactor colin...  
3  us firm 'bids for lacroix label'\n\na us firm ...  
4  stars pay tribute to actor davis\n\nhollywood ...

Replacing Upper cased characters so that the model doesn't act upon them as separate entities from their lower-case counterparts

In [9]:
def split_sentences(text):
    sentences = re.split("(\n+|\.|\.\n+|\?)",text)
    return [i for i in sentences if len(i)>3]

In [10]:
data["Sentence News Articles"] = data["Lower News Articles"].apply(split_sentences)
data["Sentence Summary"] = data["Lower Summary"].apply(split_sentences)
data["Sentence Unlike"] = data["Lower Unlike"].apply(split_sentences)

data.head()

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  
0  [top gig award for scissor sisters, new york b...  
1  [black sabbath top rock album poll, black sabb...  
2  [farrell due to make us tv debut, actor colin ...  
3  [us firm 'bids for lacroix label', a us firm h...  
4  [stars pay tribute to actor davis, hollywood s...

Splitting sentences into words to allow individual parsing

In [11]:
def remove_punctuation(text):
    cleant_text = []
    for sentence in text:
        new_sentence = ""
        for char in sentence:
            if char not in st.punctuation:
                if char=="\n":
                    new_sentence+=" "
                else:
                    new_sentence+=char
        cleant_text.append(new_sentence)
    return cleant_text

In [12]:
data["NoPunc News Articles"] = data["Sentence News Articles"].apply(remove_punctuation)
data["NoPunc Summary"] = data["Sentence Summary"].apply(remove_punctuation)
data["NoPunc Unlike"] = data["Sentence Unlike"].apply(remove_punctuation)

data.head()

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm 'bids for lacroix label', a us firm h...   
4  [stars pay tribute to actor davis, hollywood s...   

                                NoPunc News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers videoondemand, cable firms ntl a...   
4  [how to make a greener computer, the hitech in...   

                                      NoPunc Summary  \
0  [but however careful you may be if the organis...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french jordanian and nigerian nation...   
3  [cable firms ntl and telewest have both launch...   
4  [were seeing the same thing in the technology ...   

                                       NoPunc Unlike  
0  [top gig award for scissor sisters, new york b...  
1  [black sabbath top rock album poll, black sabb...  
2  [farrell due to make us tv debut, actor colin ...  
3  [us firm bids for lacroix label, a us firm has...  
4  [stars pay tribute to actor davis, hollywood s...

Removing punctuations to prevent the model from using it as a token

In [13]:
def tokenize(text):
    tokenized = []
    for sentence in text:
        tokens = re.split("\s+",sentence)
        tokenized.append(tokens)
    return tokenized

In [14]:
data["Token News Articles"] = data["NoPunc News Articles"].apply(tokenize)
data["Token Summary"] = data["NoPunc Summary"].apply(tokenize)
data["Token Unlike"] = data["NoPunc Unlike"].apply(tokenize)

data.head()

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm 'bids for lacroix label', a us firm h...   
4  [stars pay tribute to actor davis, hollywood s...   

                                NoPunc News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers videoondemand, cable firms ntl a...   
4  [how to make a greener computer, the hitech in...   

                                      NoPunc Summary  \
0  [but however careful you may be if the organis...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french jordanian and nigerian nation...   
3  [cable firms ntl and telewest have both launch...   
4  [were seeing the same thing in the technology ...   

                                       NoPunc Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm bids for lacroix label, a us firm has...   
4  [stars pay tribute to actor davis, hollywood s...

Tokenizing sentences into words

In [15]:
def remove_stopwords(text):
  return [[token for token in tokens if token not in stopwords.words("english")] for tokens in text]

In [16]:
data["Shortened News Articles"] = data["Token News Articles"].apply(remove_stopwords)
data["Shortened Summary"] = data["Token Summary"].apply(remove_stopwords)
data["Shortened Unlike"] = data["Token Unlike"].apply(remove_stopwords)

data.head(5)

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm 'bids for lacroix label', a us firm h...   
4  [stars pay tribute to actor davis, hollywood s...   

                                NoPunc News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers videoondemand, cable firms ntl a...   
4  [how to make a greener computer, the hitech in...   

                                      NoPunc Summary  \
0  [but however careful you may be if the organis...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french jordanian and nigerian nation...   
3  [cable firms ntl and telewest have both launch...   
4  [were seeing the same thing in the technology ...   

                                       NoPunc Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm bids for lacroix label, a us firm has...   
4  [stars pay tribute to actor davis, hollywood s...

Performing stopword removal helps preventing the probability distribution of a language corpus from skewing in favour of those words due to their repeated and often occurence. These stopwords also do not necessarily contribute to the projects aims. In the case of text comparison as done here, they matter relatively less compared to words that are not stop-measures.

In [17]:
def lemma_tokens(text):
    word_net = WordNetLemmatizer()
    new_text = [[word_net.lemmatize(tok) for tok in tokens] for tokens in text]
    return new_text

In [18]:
data["Lemma News Articles"] = data["Shortened News Articles"].apply(lemma_tokens)
data["Lemma Summary"] = data["Shortened Summary"].apply(lemma_tokens)
data["Lemma Unlike"] = data["Shortened Unlike"].apply(lemma_tokens)

data.head(5)

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm 'bids for lacroix label', a us firm h...   
4  [stars pay tribute to actor davis, hollywood s...   

                                NoPunc News Articles  ...  \
0  [who do you think you are, the real danger is ...  ...   
1  [fast moving phone viruses appear, security fi...  ...   
2  [seamen sail into biometric future, the luxury...  ...   
3  [cable offers videoondemand, cable firms ntl a...  ...   
4  [how to make a greener computer, the hitech in...  ...   

                                       NoPunc Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm bids for lacroix label, a us firm has...   
4  [stars pay tribute to actor davis, hollywood s...   

                                 Token News Articles  \
0  [[who, do, you, think, you, are], [the, real, ...   
1  [[fast, moving, phone, viruses, appear], [secu...   
2  [[seamen, sail, into, biometric, future], [the...   
3  [[cable, offers, videoondemand], [cable, firms...   
4  [[how, to, make, a,

Lemmatization is used to find the root of a given word, removing any prefixes or suffies present. Unlike Stemming, which would remove the 're' from 'removing' along with 'ing' to give 'mov', stemming uses context in the form of preexisting corpus and similarity metrics to give the root word 'remove' from 'removing'.

In [19]:
def pad_words(l, sentence):
    n = ["_" for i in range(l-len(sentence))]
    if sentence == []:
        return n
    return n[:len(n)//2] + sentence + n[len(n)//2:]

In [20]:
def pad(text):
    max_sentence = 259
    max_word = 259
    l = max_sentence-len(text)
    f = [pad_words(max_word,[]) for i in range(l)]
    m = [pad_words(max_word,i) for i in text]
    return f[:len(f)//2]+m+f[len(f)//2:]

In [21]:
t = {"sentence":[],"word":[]}
for i in data["Lemma News Articles"]:
    x = []
    for j in i:
        x.append(len(x))
    t["word"].append(max(x))
    t["sentence"].append(len(i))
print(max(t["word"]))
print(max(t["sentence"]))

258
259


In [22]:
data["Padded News Articles"] = data["Lemma News Articles"].apply(pad)
data["Padded Summary"] = data["Lemma Summary"].apply(pad)
data["Padded Unlike"] = data["Lemma Unlike"].apply(pad)

data.head()

News Articles  \
0  Who do you think you are?\n\nThe real danger i...   
1  Fast moving phone viruses appear\n\nSecurity f...   
2  Seamen sail into biometric future\n\nThe luxur...   
3  Cable offers video-on-demand\n\nCable firms NT...   
4  How to make a greener computer\n\nThe hi-tech ...   

                                           Summaries  \
0  But, however careful you may be, if the organi...   
1  The new strains of the Cabir mobile phone viru...   
2  She said French, Jordanian and Nigerian nation...   
3  Cable firms NTL and Telewest have both launche...   
4  We're seeing the same thing in the technology ...   

                                              Unlike  \
0  Top gig award for Scissor Sisters\n\nNew York ...   
1  Black Sabbath top rock album poll\n\nBlack Sab...   
2  Farrell due to make US TV debut\n\nActor Colin...   
3  US firm 'bids for Lacroix label'\n\nA US firm ...   
4  Stars pay tribute to actor Davis\n\nHollywood ...   

                                 Lower News Articles  \
0  who do you think you are?\n\nthe real danger i...   
1  fast moving phone viruses appear\n\nsecurity f...   
2  seamen sail into biometric future\n\nthe luxur...   
3  cable offers video-on-demand\n\ncable firms nt...   
4  how to make a greener computer\n\nthe hi-tech ...   

                                       Lower Summary  \
0  but, however careful you may be, if the organi...   
1  the new strains of the cabir mobile phone viru...   
2  she said french, jordanian and nigerian nation...   
3  cable firms ntl and telewest have both launche...   
4  we're seeing the same thing in the technology ...   

                                        Lower Unlike  \
0  top gig award for scissor sisters\n\nnew york ...   
1  black sabbath top rock album poll\n\nblack sab...   
2  farrell due to make us tv debut\n\nactor colin...   
3  us firm 'bids for lacroix label'\n\na us firm ...   
4  stars pay tribute to actor davis\n\nhollywood ...   

                              Sentence News Articles  \
0  [who do you think you are, the real danger is ...   
1  [fast moving phone viruses appear, security fi...   
2  [seamen sail into biometric future, the luxury...   
3  [cable offers video-on-demand, cable firms ntl...   
4  [how to make a greener computer, the hi-tech i...   

                                    Sentence Summary  \
0  [but, however careful you may be, if the organ...   
1  [the new strains of the cabir mobile phone vir...   
2  [she said french, jordanian and nigerian natio...   
3  [cable firms ntl and telewest have both launch...   
4  [we're seeing the same thing in the technology...   

                                     Sentence Unlike  \
0  [top gig award for scissor sisters, new york b...   
1  [black sabbath top rock album poll, black sabb...   
2  [farrell due to make us tv debut, actor colin ...   
3  [us firm 'bids for lacroix label', a us firm h...   
4  [stars pay tribute to actor davis, hollywood s...   

                                NoPunc News Articles  ...  \
0  [who do you think you are, the real danger is ...  ...   
1  [fast moving phone viruses appear, security fi...  ...   
2  [seamen sail into biometric future, the luxury...  ...   
3  [cable offers videoondemand, cable firms ntl a...  ...   
4  [how to make a greener computer, the hitech in...  ...   

                                        Token Unlike  \
0  [[top, gig, award, for, scissor, sisters], [ne...   
1  [[black, sabbath, top, rock, album, poll], [bl...   
2  [[farrell, due, to, make, us, tv, debut], [act...   
3  [[us, firm, bids, for, lacroix, label], [a, us...   
4  [[stars, pay, tribute, to, actor, davis], [hol...   

                             Shortened News Articles  \
0  [[think], [real, danger, happens, data, crosse...   
1  [[fast, moving, phone, viruses, appear], [secu...   
2  [[seamen, sail, biometric, future], [luxury, c...   
3  [[cable, offers, videoondemand], [cable, firms...   
4  [[make, greener, co

Padding is done to ensure that there is uniformity in the input sizes

In [23]:
def convert(text):
    x = ["%".join(sent) for sent in text]
    return "^".join(x)

In [24]:
data["News Articles"] = data["Lemma News Articles"].apply(convert)
data["Summary"] = data["Lemma Summary"].apply(convert)
data["Unlike"] = data["Lemma Unlike"].apply(convert)

In [25]:
data.drop([i for i in data.columns if i not in["News Articles","Summary","Unlike"]],inplace = True, axis = 1)
data.head()

News Articles  \
0  think^real%danger%happens%data%cross%net%argue...   
1  fast%moving%phone%virus%appear^security%firm%w...   
2  seaman%sail%biometric%future^luxury%cruise%lin...   
3  cable%offer%videoondemand^cable%firm%ntl%telew...   
4  make%greener%computer^hitech%industry%starting...   

                                              Unlike  \
0  top%gig%award%scissor%sister^new%york%band%sci...   
1  black%sabbath%top%rock%album%poll^black%sabbat...   
2  farrell%due%make%u%tv%debut^actor%colin%farrel...   
3  u%firm%bid%lacroix%label^u%firm%said%final%neg...   
4  star%pay%tribute%actor%davis^hollywood%star%in...   

                                             Summary  
0  however%careful%may%organisation%trust%persona...  
1  new%strain%cabir%mobile%phone%virus%use%shortr...  
2  said%french%jordanian%nigerian%national%would%...  
3  cable%firm%ntl%telewest%launched%videoondemand...  
4  seeing%thing%technology%industry%result%billio...

In [26]:
data.to_csv("preprocessed_data.csv")

Moving the preprocessed data to a csv file from which it can be accessed in other locations